<link rel="stylesheet" href="../../styles/theme_style.css">
<!--link rel="stylesheet" href="../../styles/header_style.css"-->
<link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/4.7.0/css/font-awesome.min.css">

<table width="100%">
    <tr>
        <td id="image_td" width="15%" class="header_image_color_5"><div id="image_img"
        class="header_image_5"></div></td>
        <td class="header_text"> Detection of Outliers </td>
    </tr>
</table>

<div id="flex-container">
    <div id="diff_level" class="flex-item">
        <strong>Difficulty Level:</strong>   <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star"></span>
    </div>
    <div id="tag" class="flex-item-tag">
        <span id="tag_list">
            <table id="tag_list_table">
                <tr>
                    <td class="shield_left">Tags</td>
                    <td class="shield_right" id="tags">detect&#9729;outliers&#9729;algorithms</td>
                </tr>
            </table>
        </span>
        <!-- [OR] Visit https://img.shields.io in order to create a tag badge-->
    </div>
</div>

Outliers are events that do not conform with the rest of a dataset. The detection of such events might be important to denoise parts of signals, detect unexpected events, remove movement artifacts, among other applications.

The difficulty of this detection is the fact that generic algorithms may yield low accuracy for different signals and different kinds of outliers.

In this <strong class="color4">Jupyter Notebook</strong> we will present three different approaches to this problem and discuss how each may be more suited for different situations.

<hr>

## 1 - Import of the required packages
These packages will facilitate outlier detection.

In [1]:
# Import biosignalsnotebooks Python package
import biosignalsnotebooks as bsnb

# Import numpy
from numpy import array, histogram, mean, std, ptp, hstack

# Import scit-kit learn
from sklearn.cluster import DBSCAN

# Import Kurtosis from scipy package
from scipy.stats import kurtosis

# Package used for forecasting tasks
from statsmodels.tsa.arima.model import ARIMA

# Function intended to estimate the Euclidean distance between forecast and the original signal
from scipy.spatial import distance

In [2]:
# Imports used on hidden cells
import warnings
warnings.filterwarnings('ignore')
from numpy import zeros, arange, concatenate

## 2 - Load the signals
In this notebooks we will use a ECG signal that is contaminated with motion artifacts. So, in this case, the outliers will be the motion artifacts.

In [3]:
# Load the signal and the header of the file, which contains information about the acquisition.
data, header = bsnb.load("../data/ECG-ejer_andrea.h5", get_header=True)

# The ECG signal was acquired in channel 2 of the hub, thus we must load it from the Python dictionary using the CH2 key.
signal_raw = array(data['CH2'])

# From the header we can extract information such as the sampling rate and resolution
sampling_frequency = header['sampling rate']

# The following line allows to generate the time axis of the axis based on the utilized sampling frequency.
time = bsnb.generate_time(signal_raw, sample_rate=sampling_frequency)

The next plot shows the signal (filtered to remove high frequency noise), where the motion artifacts are identified by red vertical bands.

In [10]:
# Remove low frequency noise
signal_raw = bsnb.highpass(signal_raw, 0.2, use_filtfilt=True)

from bokeh.models import BoxAnnotation
from bokeh.plotting import show

# Define the box for the first artifact
first_box = BoxAnnotation(left=4.1, right=7.61, fill_alpha=0.1, fill_color='red')

# Define the box for the second artifact
second_box = BoxAnnotation(left=13.91, right=16.52, fill_alpha=0.1, fill_color='red')

# Plot the ECG signal
plot_artifacts = bsnb.plot(time, signal_raw, y_axis_label="ECG(a.u.)", get_fig_list=True, show_plot=False)[0]

# Add the boxes that define the outliers
plot_artifacts.add_layout(first_box)
# plot_artifacts.add_layout(second_box)
plot_artifacts.add_layout(second_box)

# Show the plot
show(plot_artifacts)

## 3 - Outliers Detection Approaches
Outliers detection can be made using different approaches. In this section, we will demonstrate three of the most common, starting by a statistical approach, followed by a forecasting approach and finishing with an approach based on unsupervised machine learning.

### 3.1 - Statistical Approach
Statistically, outliers correspond to the events that have a lower probability of happening. Thus, we will plot the histogram of the signal and try to identify the outliers by that. Note that, in this case, only the points that are deviated from the mean will be considered outliers.

In [5]:
from bokeh.plotting import figure

hist, edges = histogram(signal_raw, bins = 100)

p = figure(background_fill_color=(242, 242, 242))
p.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:], fill_color="#00893E", line_color="white", alpha=0.5);

mean_value = mean(signal_raw)
std_value = std(signal_raw)

In [6]:
# This cell serves only to style the histogram plot
from bokeh.plotting import show
from bokeh.models.tools import PanTool, ResetTool, BoxZoomTool, WheelZoomTool
from bokeh.models import Span

# Vertical line
vline = Span(location=mean_value, dimension='height', line_color='black', line_width=1)
vline1 = Span(location=mean_value+std_value, dimension='height', line_color='grey', line_width=2, line_dash='dashed')
vline2 = Span(location=mean_value-std_value, dimension='height', line_color='grey', line_width=2, line_dash='dashed')
p.renderers.extend([vline, vline1, vline2])


toolbar="right"
p.toolbar.active_scroll = p.select_one(WheelZoomTool)
p.sizing_mode = 'scale_width'
p.height = 200
p.toolbar.logo = None
p.toolbar_location = toolbar
p.xaxis.axis_label = "Value"
p.yaxis.axis_label = "# Points"

p.xgrid.grid_line_color = (150, 150, 150)
p.ygrid.grid_line_color = (150, 150, 150)

p.xgrid.grid_line_dash = [2, 2]

p.xaxis.major_tick_line_color = "white"
p.xaxis.minor_tick_line_color = "white"
p.xaxis.axis_line_color = "white"
p.yaxis.major_tick_in = 0
p.yaxis.major_tick_out = 0

p.yaxis.major_tick_line_color = "white"
p.yaxis.minor_tick_line_color = "white"
p.yaxis.minor_tick_in = 0
p.yaxis.minor_tick_out = 0
p.yaxis.axis_line_color = (150, 150, 150)
p.yaxis.axis_line_dash = [2, 2]

p.yaxis.major_label_text_color = (88, 88, 88)
p.xaxis.major_label_text_color = (88, 88, 88)

p.ygrid.grid_line_dash = [2, 2]
show(p)

The histogram shows the distribution of values of the signal. The black vertical line corresponds to the mean value and the dashed lines to the standard deviation relative to the mean. One approach could be to consider all values below or above the range of the standard deviation as outliers. 

This idea can be graphically demonstrated below:

In [11]:
from bokeh.models import BoxAnnotation
from bokeh.plotting import show

sup_limit = mean_value + std_value
sub_limit = mean_value - std_value

# Plot the ECG signal
sup_std = zeros(len(time)) + sup_limit
sub_std = zeros(len(time)) + sub_limit

bsnb.plot([time, time, time], [signal_raw, sup_std, sub_std], y_axis_label="ECG(a.u.)")

In this case, outliers are all the points that are not in between the two horizontal lines. Thus, we get some false positives because we are not taking into account the time domain of the signal and its context. While we could clearly set thresholds to identify the peaks that are outliers, the parts of those peaks that do not cross the thresholds but still correspond to artifacts could never be considered as outliers.

### 3.2 - Forecasting Approach
As we are dealing with time series, context is an important aspect to take into account for outliers detection. In this section, we will show how to take the time axis into consideration, by using forecasting models for outliers detection.

Forecasting models attempt to capture the normal behaviour of a time series and then forecast that same behaviour in the future. For outliers detection, if the forecast model is accurate enough, one can compare the actual data with the forecast of previous data and, if it is too different, it is considered an outlier.

<strong class="color2">Note</strong>: In this case, we will not analyse the accuracy of the forecasting model and we will assume it is accurate <i>enough</i>.

There are numerous algorithms that may be capable to forecast time series, as enumerate in this <a href="https://machinelearningmastery.com/time-series-forecasting-methods-in-python-cheat-sheet/">link <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a>. We chose to apply the <strong class="color7">Autoregressive Integrated Moving Average (ARIMA)</strong> model because it combines two others, <strong>autoregression (AR)</strong> and <strong>moving average (MA)</strong>, after differencing the signal to make the time series stationary. For this, we will use the algorithm implemented in the <strong class="color4">statsmodels</strong> Python package.

#### 3.2.1 - Comparing Outliers to Normal Results
In this subsection we will present the methodology followed to detect outliers and compare the results of this procedure for outliers and normal points.

First, we will present the case of an outlier. In this case we will show the case of the motion artifact starting at around 14 seconds (hence <strong><span class="color2">j = 14*sampling_frequency</span></strong>). The order of the model was taken from experimenting with various orders and saving the one with the best score.

In [8]:
# We will train our model with the signal until the 14th second
j = 14*sampling_frequency

# In the next line we build the model with data until the 14th second and define the order of the model
model = ARIMA(signal_raw[:j], order=(3, 0, 3))

# In the next cell the model is fitted to the data that we gave as input
model_fit = model.fit()

The next step, since we already trained (fitted) our model to the input data, is to compute the forecast for the next time steps. In this case, we chose to forecast for the next 0.5 seconds. Note that the quality of the forecast degrades with the duration of that forecast. Thus, typically, the longer forecasts, the worse their quality.

In [9]:
# Compute the forecast
yhat_0 = model_fit.forecast(steps=int(0.5*sampling_frequency))[0]
yhat = model_fit.forecast(steps=int(0.5*sampling_frequency))

In the next plot, we show the forecast (around the second 14 with a duration of 0.5 seconds). Then, we present the result of the Euclidean distance to the actual signal.

In [12]:
bsnb.plot([time, time[j:j+int(0.5*sampling_frequency)]], [signal_raw, yhat], y_axis_label="ECG(a.u.)")
print("For this particular segment, which is an outlier, the Euclidean distance between the expected the result and the real is {:0.2f}.".format(distance.euclidean(signal_raw[j:j+500], yhat)))

For this particular segment, which is an outlier, the Euclidean distance between the expected the result and the real is 1200.60.


Next, we will repeat the same procedure but for a normal interval. After this, we will compare the results of the Euclidean distances and discuss the suitability of this methodology.

In this case, we use the signal until 2 seconds, so make sure to check that part of the signal on the following plot.

In [13]:
# We will train our model with the signal until de index 2000
j = 2*sampling_frequency
model = ARIMA(signal_raw[:j], order=(3, 0, 3))
model_fit = model.fit()

In [14]:
# make prediction
yhat_0 = model_fit.forecast(steps=int(0.5*sampling_frequency))[0]
yhat = model_fit.forecast(steps=int(0.5*sampling_frequency))

In [15]:
bsnb.plot([time, time[j:j+int(0.5*sampling_frequency)]], [signal_raw, yhat], y_axis_label="ECG(a.u.)")
print("For this particular segment, which is normal, the Euclidean distance between the expected the result and the real is {:0.2f}.".format(distance.euclidean(signal_raw[j:j+500], yhat)))

For this particular segment, which is normal, the Euclidean distance between the expected the result and the real is 1088.94.


As expected, considering that the forecast is accurate enough, the distance between the forecast values and the actual signal is lower for the normal segment than for the outlier, because the forecast is not able to predict an anomalous event. Thus, if we apply this to the whole signal, hopefully we will be able to detect the outliers in our signal.

#### 3.2.2 - Applying the Procedure to the whole Signal
Given the clear differences between the normal segment and the outlier, we propose to apply the same methodology to the whole signal. In this case, we will consider that the state (normal or outlier) does not change in a 1 second range, thus we will apply the forecast every second. For each time we forecast the next second of signal, we compute the Euclidean distance between the predicted signal and the actual signal and store it in a list.

<strong class="color7">Note:</strong> We will start at 2 seconds because ARIMA model needs data to capture the normal behaviour of the signal.

In [37]:
'''
# Start
num = 2*sampling_frequency

# Definition of the step
step = 1*sampling_frequency

# Initialise the list to store the values of the Euclidean distance between forecasts and the signal
diff = []

# Helper variable to keep track of the progress
j=0

# Loop the values of signal, with a step of 1 second, to compute the forecast
for i in range(num, len(signal_raw), step):
    # Print the progress of the loop
    print("{:0.2f}% completed".format((j*step*100)/(len(signal_raw)-num)))
    
    # Copy the ECG signal to a new variable
    data = signal_raw.copy()
    
    # Define the model (similar to the previous subsections)
    model = ARIMA(data[:i], order=(3, 0, 3))
    
    # try...except because the model could give some unexpected error
    try:
        # Fit the model
        model_fit = model.fit()
        
        # Forecast the next 1 second of the signal
        yhat = model_fit.forecast(steps=step)[0]
        
        # Compute the Euclidean distance between the forecast and the signal
        euc_distance = distance.euclidean(data[i:i+step], yhat)
        # Store the Euclidean distances
        diff.append(euc_distance)
    except ValueError as e:
        # If a ValueError occurs, print the error
        print(e)
    finally:
        # Increment the helper variable to keep track of the progress
        j+=1
'''

0.00% completed


Prediction must have `end` after `start`.
5.18% completed
Prediction must have `end` after `start`.
10.36% completed
Prediction must have `end` after `start`.
15.54% completed
Prediction must have `end` after `start`.
20.73% completed
Prediction must have `end` after `start`.
25.91% completed
Prediction must have `end` after `start`.
31.09% completed
Prediction must have `end` after `start`.
36.27% completed
Prediction must have `end` after `start`.
41.45% completed
Prediction must have `end` after `start`.
46.63% completed
Prediction must have `end` after `start`.
51.81% completed
Prediction must have `end` after `start`.
56.99% completed
Prediction must have `end` after `start`.
62.18% completed
Prediction must have `end` after `start`.
67.36% completed
Prediction must have `end` after `start`.
72.54% completed
Prediction must have `end` after `start`.
77.72% completed
Prediction must have `end` after `start`.
82.90% completed
Prediction must have `end` after `start`.
88.08% complete

The next plot contains lots of information: 
<ul>
    <li>Signal</li>
    <li>Euclidean distance of each segment</li>
    <li>An horizontal line, which corresponds to the threshold we set</li>
</ul>
Those are normalized in order to be comparable. As shown, the distance of outliers to the forecast are higher than the distance of normal segments. Thus, we set a threshold at around <strong><span class="color2">0.22</span></strong>, which is able to accurately distinguish normal segments and outliers, that are identified by the red bands in the graph.

In [38]:
'''
diff_vector = []
for value in diff:
    diff_vector.append(zeros(step)+value)

diff_vector = concatenate(diff_vector)
threshold = 0.22

# Normalize both vectors
diff_vector_normalized = diff_vector / ptp(diff_vector)
signal_norm = signal_raw / ptp(signal_raw)

start = len(time)-len(diff_vector_normalized)
plot_diff = bsnb.plot([time, time[start-step:-step]], [signal_norm, diff_vector_normalized], hor_lines=[[threshold], [threshold]], get_fig_list=True, show_plot=False)[0]

for i in range(len(diff)):
    if diff[i]/ptp(diff) > threshold:
        _aux = BoxAnnotation(left=(start-step+i*step)/sampling_frequency, right=(start-step+(i+1)*step)/sampling_frequency, fill_alpha=0.2, fill_color='red')
        # Add the boxes that define the outliers
        plot_diff.add_layout(_aux)

# Show the plot
show(plot_diff)
'''

ValueError: need at least one array to concatenate

Though this method is accurate, it has some limitations. There are numerous algorithms to chose from that may suit the data in different ways and, it might not be easy to determine which is better. Furthermore, for the ARIMA model we need to set the order of the model, which involves a time-consuming process. Moreover, the definition of the place to start the training of the model and the step is a process that needs to be taken into account for every algorithm used in this type of application. Besides, setting a threshold may not be the better approach, as it may be too simplistic depending on the quality of data. Finally, the fit of the model is time consuming process, which should be made offline.

However, as demonstrated, it may be a reliable method to detect outliers in time series data.

### 3.3 - Unsupervised Machine Learning Approach
In this section, we will show how to use unsupervised machine learning for outliers detection, namely using the <a href="https://scikit-learn.org/stable/">scikit-learn <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a> Python package. If you are not familiar with machine learning, we recommend you to read the notebooks of the category <a href="https://www.biosignalsplux.com/notebooks/Categories/MainFiles/biosignalsnotebooks_rev.php">Train and Classify <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a>.

For this application, we will segment our signal in equal parts. For that, we will use the <strong><span class="color2">biosignalsnotebooks</span></strong> Python package, in which the only parameter that we need is the time that each segment (or window) of the signal should have. This is an arbitrary parameter, so we chose 1 second.

In [16]:
time_window = 1 # second

data_segments = bsnb.windowing(signal_raw, sampling_frequency, time_window)

In [17]:
# Vertical line
segments = arange(0, time[-1], time_window)
vlines = []
for segment in segments:
    vlines.append(Span(location=segment, dimension='height', line_color='grey', line_width=2, line_dash='dashed'))

p = bsnb.plot(time, signal_raw, get_fig_list=True, show_plot=False, y_axis_label="ECG(a.u.)")[0]
p.renderers.extend(vlines)
show(p)

After segmenting the signal, we will extract features that may separate the outliers from the normal segments of the signal. We chose to use only two features, <strong><span class="color2">standard deviation</span></strong> and <strong><span class="color5">kurtosis</span></strong>, for visualization and simplicity sake, but we could use virtually the number of features we wanted. Note however, that the increase of the number of features, also increases the complexity of the analysis. Next, we will plot the features from each segment and we can perceive that there are points that are far more sparse than others, which might correspond to outliers.

In [18]:
func = [std, kurtosis]
data_features = bsnb.features_extraction(data_segments, func)

In [19]:
p = figure(background_fill_color=(242, 242, 242))

# add a circle renderer with a size, color, and alpha
p.circle(data_features[:,0], data_features[:,1], size=15, color="#009EE3", alpha=.9)

toolbar="right"
p.toolbar.active_scroll = p.select_one(WheelZoomTool)
p.sizing_mode = 'scale_width'
p.height = 200
p.toolbar.logo = None
p.toolbar_location = toolbar
p.xaxis.axis_label = "Standard Deviation"
p.yaxis.axis_label = "Kurtosis"

p.xgrid.grid_line_color = (150, 150, 150)
p.ygrid.grid_line_color = (150, 150, 150)

p.xgrid.grid_line_dash = [2, 2]

p.xaxis.major_tick_line_color = "white"
p.xaxis.minor_tick_line_color = "white"
p.xaxis.axis_line_color = "white"
p.yaxis.major_tick_in = 0
p.yaxis.major_tick_out = 0

p.yaxis.major_tick_line_color = "white"
p.yaxis.minor_tick_line_color = "white"
p.yaxis.minor_tick_in = 0
p.yaxis.minor_tick_out = 0
p.yaxis.axis_line_color = (150, 150, 150)
p.yaxis.axis_line_dash = [2, 2]

p.yaxis.major_label_text_color = (88, 88, 88)
p.xaxis.major_label_text_color = (88, 88, 88)

p.ygrid.grid_line_dash = [2, 2]

# show the results
show(p)

For this example, we will use the <strong class="color13">DBSCAN (Density-Based Spatial Clustering of Applications with Noise)</strong> algorithm, which clusters data points based on their <strong class="color4">density</strong> relative to others. Essentially, this algorithm clusters points in two types: belonging to clusters (considered <strong class="color1">core points</strong>) or <strong class="color10">outliers</strong>. To belong to a cluster, a data point must have a number <strong><i>n</i> points</strong> at a <strong>distance below <i>dist</i></strong> or belong to the vicinity of a core point. All points that do not conform to this criteria are considered outliers. Thus, this algorithm receives two parameters (<i>n</i> and <i>dist</i>) that need to be tuned to accurately be applied.

<strong class="color7">Note</strong>: <i>We will first normalize the features, so that no features is more important than the other.</i>

In [20]:
# Normalise the features, so that they end up with a range of 1.
data_std_normalized = data_features[:, 0] / ptp(data_features[:, 0])
data_kurtosis_normalized = data_features[:, 1] / ptp(data_features[:, 1])

# Constructing the normalized features vector. The .reshape(-1, 1) is used to transpose the line arrays to column arrays.
data_features_normalized = hstack([data_std_normalized.reshape(-1, 1), data_kurtosis_normalized.reshape(-1, 1)])

# Definition of the parameters for the DBSCAN algorithm
dist = .05
n = 3

# Definition of the algorithm
outlier_detection = DBSCAN(min_samples = n, eps = dist)

# Application of the algorithm to our features matrix
clusters = outlier_detection.fit_predict(data_features_normalized)

In [21]:
from numpy import where

outliers = data_features_normalized[where(clusters == -1)[0]]
normal = data_features_normalized[where(clusters != -1)[0]]

p = figure(background_fill_color=(242, 242, 242))

# add a circle renderer with a size, color, and alpha
p.circle(normal[:,0], normal[:,1], size=15, color="#009EE3", alpha=.9)

toolbar="right"
p.toolbar.active_scroll = p.select_one(WheelZoomTool)
p.sizing_mode = 'scale_width'
p.height = 200
p.toolbar.logo = None
p.toolbar_location = toolbar
p.xaxis.axis_label = "Value"
p.yaxis.axis_label = "# Points"

p.xgrid.grid_line_color = (150, 150, 150)
p.ygrid.grid_line_color = (150, 150, 150)

p.xgrid.grid_line_dash = [2, 2]

p.xaxis.major_tick_line_color = "white"
p.xaxis.minor_tick_line_color = "white"
p.xaxis.axis_line_color = "white"
p.yaxis.major_tick_in = 0
p.yaxis.major_tick_out = 0

p.yaxis.major_tick_line_color = "white"
p.yaxis.minor_tick_line_color = "white"
p.yaxis.minor_tick_in = 0
p.yaxis.minor_tick_out = 0
p.yaxis.axis_line_color = (150, 150, 150)
p.yaxis.axis_line_dash = [2, 2]

p.yaxis.major_label_text_color = (88, 88, 88)
p.xaxis.major_label_text_color = (88, 88, 88)

p.ygrid.grid_line_dash = [2, 2]

p.circle(outliers[:, 0], outliers[:, 1], size = 15, color = 'red')
show(p)

The next plot will show at what segments do those points correspond in the actual signal.

In [22]:
# Plot the ECG signal
plot_outliers = bsnb.plot(time, signal_raw, get_fig_list=True, show_plot=False)[0]

for i in range(len(clusters)):
    if clusters[i] < 0:
        _aux = BoxAnnotation(left=segments[i], right=segments[i+1], fill_alpha=0.1, fill_color='red')
        # Add the boxes that define the outliers
        plot_outliers.add_layout(_aux)

# Show the plot
show(plot_outliers)

This method yielded accurate results as it was able to identify the motion artifacts that we had previously determined. However, note that we had to tune all the parameters: the time for the segments of the signal, the features we used to distinguish outliers from normal segments and the parameters for the DBSCAN algorithm. Furthermore, it is not applicable in real time application as it requires the whole dataset to calculate the density of each point.

In this notebook we made a quick review of three different methods to detect outliers in time series data. Though forecasting and unsupervised machine learning methods may have high accuracy when detecting outliers, they are also very complex and involve the determination of numerous parameters which might affect the results and, thus, must be carefully applied.

You are now in conditions to start exploring the fascination world of outliers detection and all the algorithms that are commonly applied to this problem.

<strong><span class="color7">We hope that you have enjoyed this guide. </span><span class="color2">biosignalsnotebooks</span><span class="color4"> is an environment in continuous expansion, so don't stop your journey and learn more with the remaining <a href="../MainFiles/biosignalsnotebooks.ipynb">Notebooks <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a></span></strong> ! 